In [47]:
import pandas as pd
import sklearn as sk
import matplotlib.pyplot as plt
import json
import math

In [48]:
cf_2018 = pd.read_csv('flight_data/Combined_Flights_2018.csv')
cf_2018.head()

FlightDate            Airline Origin Dest  Cancelled  Diverted  CRSDepTime  \
0  2018-01-23  Endeavor Air Inc.    ABY  ATL      False     False        1202   
1  2018-01-24  Endeavor Air Inc.    ABY  ATL      False     False        1202   
2  2018-01-25  Endeavor Air Inc.    ABY  ATL      False     False        1202   
3  2018-01-26  Endeavor Air Inc.    ABY  ATL      False     False        1202   
4  2018-01-27  Endeavor Air Inc.    ABY  ATL      False     False        1400   

   DepTime  DepDelayMinutes  DepDelay  ...  WheelsOff  WheelsOn  TaxiIn  \
0   1157.0              0.0      -5.0  ...     1211.0    1249.0     7.0   
1   1157.0              0.0      -5.0  ...     1210.0    1246.0    12.0   
2   1153.0              0.0      -9.0  ...     1211.0    1251.0    11.0   
3   1150.0              0.0     -12.0  ...     1207.0    1242.0    11.0   
4   1355.0              0.0      -5.0  ...     1412.0    1448.0    11.0   

   CRSArrTime  ArrDelay  ArrDel15  ArrivalDelayGroups  ArrTimeBlk  \
0        1304      -8.0       0.0                -1.0   1300-1359   
1        1304      -6.0       0.0                -1.0   1300-1359   
2        1304      -2.0       0.0                -1.0   1300-1359   
3        1304     -11.0       0.0                -1.0   1300-1359   
4        1500      -1.0       0.0                -1.0   1500-1559   

   DistanceGroup  DivAirportLandings  
0              1                 0.0  
1              1                 0.0  
2              1                 0.0  
3              1                 0.0  
4              1                 0.0  

[5 rows x 61 columns]

In [49]:
# Filter the dataframe to include only the delays from ATL
import RegressionModel

filtered_df = cf_2018[(cf_2018['Origin'] == 'JFK')]

RegressionModel.destinations = list(cf_2018['DestCityName'].unique())

In [50]:
relevant_columns = ['FlightDate', 'Dest', 'DepDelayMinutes', 'ArrDelayMinutes']
jfk_flights_2018 = filtered_df[relevant_columns]
jfk_flights_2018.dropna(inplace=True)

C:\Users\s2080\AppData\Local\Temp\ipykernel_13776\3101909741.py:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  jfk_flights_2018.dropna(inplace=True)


In [51]:
jfk_flights_2018

FlightDate Dest  DepDelayMinutes  ArrDelayMinutes
5544     2018-01-22  SJC              0.0              0.0
5547     2018-01-22  MSY             86.0             77.0
5548     2018-01-22  JAX             29.0             11.0
5554     2018-01-22  ROC              0.0              0.0
5565     2018-01-22  BUF              0.0              0.0
...             ...  ...              ...              ...
5666920  2018-09-10  SFO              0.0              3.0
5666921  2018-09-10  MSP              0.0              0.0
5667057  2018-09-10  LAX             13.0              0.0
5667231  2018-09-10  SEA             48.0             44.0
5672362  2018-09-04  BNA              0.0              0.0

[83754 rows x 4 columns]

In [52]:
# Convert 'FlightDate' into numerical components
jfk_flights_2018['FlightDate'] = pd.to_datetime(jfk_flights_2018['FlightDate'])
jfk_flights_2018['Year'] = jfk_flights_2018['FlightDate'].dt.year
jfk_flights_2018['Month'] = jfk_flights_2018['FlightDate'].dt.month
jfk_flights_2018['Day'] = jfk_flights_2018['FlightDate'].dt.day

# One-hot encoding for categorical variables
df_jfk_encoded = pd.get_dummies(jfk_flights_2018, columns=['Dest'])


C:\Users\s2080\AppData\Local\Temp\ipykernel_13776\149138236.py:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  jfk_flights_2018['FlightDate'] = pd.to_datetime(jfk_flights_2018['FlightDate'])
C:\Users\s2080\AppData\Local\Temp\ipykernel_13776\149138236.py:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  jfk_flights_2018['Year'] = jfk_flights_2018['FlightDate'].dt.year
C:\Users\s2080\AppData\Local\Temp\ipykernel_13776\149138236.py:4: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice fr

In [53]:
from sklearn.model_selection import train_test_split

# Choose your target variable, e.g., 'DepDelayMinutes'
X = df_jfk_encoded.drop('DepDelayMinutes', axis=1)
y = df_jfk_encoded['DepDelayMinutes']

# Splitting the dataset into training and testing sets
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.2, random_state=42)

X_train = X_train.apply(pd.to_numeric, errors='coerce')
y_train = pd.to_numeric(y_train, errors='coerce')
X_test = X_test.apply(pd.to_numeric, errors='coerce')
y_test = pd.to_numeric(y_test, errors='coerce')

In [54]:
from sklearn.linear_model import LinearRegression

# Initialize the model
model = LinearRegression()

# Train the model
model.fit(X_train, y_train)


LinearRegression()

In [56]:
from sklearn.metrics import mean_squared_error, r2_score

# Predict on the test set
y_pred = model.predict(X_test)

# Evaluate the model
mse = mean_squared_error(y_test, y_pred)
r2 = r2_score(y_test, y_pred)
print("Mean Squared Error:", mse)
print("R^2 Score:", r2)


Mean Squared Error: 169.08504182894654
R^2 Score: 0.9198498663312777


In [63]:
print(list(X_test))

['FlightDate', 'ArrDelayMinutes', 'Year', 'Month', 'Day', 'Dest_ABQ', 'Dest_ACK', 'Dest_ATL', 'Dest_AUS', 'Dest_BGR', 'Dest_BNA', 'Dest_BOS', 'Dest_BQN', 'Dest_BTV', 'Dest_BUF', 'Dest_BUR', 'Dest_BWI', 'Dest_CHS', 'Dest_CLE', 'Dest_CLT', 'Dest_CMH', 'Dest_CVG', 'Dest_DAB', 'Dest_DCA', 'Dest_DEN', 'Dest_DFW', 'Dest_DTW', 'Dest_EGE', 'Dest_FLL', 'Dest_HNL', 'Dest_HOU', 'Dest_HYA', 'Dest_IAD', 'Dest_IND', 'Dest_JAC', 'Dest_JAX', 'Dest_LAS', 'Dest_LAX', 'Dest_LGB', 'Dest_MCO', 'Dest_MIA', 'Dest_MSP', 'Dest_MSY', 'Dest_MVY', 'Dest_OAK', 'Dest_ONT', 'Dest_ORD', 'Dest_ORF', 'Dest_ORH', 'Dest_PBI', 'Dest_PDX', 'Dest_PHL', 'Dest_PHX', 'Dest_PIT', 'Dest_PSE', 'Dest_PSP', 'Dest_PWM', 'Dest_RDU', 'Dest_RIC', 'Dest_RNO', 'Dest_ROC', 'Dest_RSW', 'Dest_SAN', 'Dest_SAT', 'Dest_SAV', 'Dest_SEA', 'Dest_SFO', 'Dest_SJC', 'Dest_SJU', 'Dest_SLC', 'Dest_SMF', 'Dest_SNA', 'Dest_SRQ', 'Dest_STT', 'Dest_SYR', 'Dest_TPA']


In [83]:

i = X_test.iloc[[3]].copy()
i['FlightDate'] = 1640995200000000000
i['Year'] = 2022
i['Month'] = 1
i['Day'] = 1
print(i)


                 FlightDate  ArrDelayMinutes  Year  Month  Day  Dest_ABQ  \
436014  1640995200000000000              0.0  2022      1    1     False   

        Dest_ACK  Dest_ATL  Dest_AUS  Dest_BGR  ...  Dest_SFO  Dest_SJC  \
436014     False      True     False     False  ...     False     False   

        Dest_SJU  Dest_SLC  Dest_SMF  Dest_SNA  Dest_SRQ  Dest_STT  Dest_SYR  \
436014     False     False     False     False     False     False     False   

        Dest_TPA  
436014     False  

[1 rows x 76 columns]


In [67]:
X_mike = X_test.iloc[[3]]

In [84]:
model.predict(i)

array([-26.49915968])